Homework 7

7.1  Create a crawler using the webcrawler provided and discussed in my jupyter notebook ( https://github.com/pschragger/big-data-python-class/blob/master/Lectures/Lecture_7_-_Link_Analysis.ipynb) , have it crawl the first 200 pages from a base URL of your choosing

In [2]:
cd C:/Users/Sam/big-data-python-class/Homeworks/Homework7/

C:\Users\Sam\big-data-python-class\Homeworks\Homework7


Inititializing the project:

In [3]:
%%cmd
scrapy startproject datablogger_scraper

Microsoft Windows [Version 10.0.17134.345]
(c) 2018 Microsoft Corporation. All rights reserved.

(base) C:\Users\Sam\big-data-python-class\Homeworks\Homework7>scrapy startproject datablogger_scraper
New Scrapy project 'datablogger_scraper', using template directory 'C:\\Users\\Sam\\Anaconda2\\lib\\site-packages\\scrapy\\templates\\project', created in:
    C:\Users\Sam\big-data-python-class\Homeworks\Homework7\datablogger_scraper

You can start your first spider with:
    cd datablogger_scraper
    scrapy genspider example example.com

(base) C:\Users\Sam\big-data-python-class\Homeworks\Homework7>

In [3]:
cd datablogger_scraper

C:\Users\Sam\big-data-python-class\Homeworks\Homework7\datablogger_scraper


Generating a spider inside the project folder. This creates a python file with default code for a spider which can be edited.

In [24]:
%%cmd
scrapy genspider datablogger data-blogger.com

Microsoft Windows [Version 10.0.17134.345]
(c) 2018 Microsoft Corporation. All rights reserved.

(base) C:\Users\Sam\big-data-python-class\Homeworks\Homework7\datablogger_scraper>scrapy genspider datablogger data-blogger.com
Created spider 'datablogger' using template 'basic' in module:
  datablogger_scraper.spiders.datablogger

(base) C:\Users\Sam\big-data-python-class\Homeworks\Homework7\datablogger_scraper>

In [4]:
cd datablogger_scraper/

C:\Users\Sam\big-data-python-class\Homeworks\Homework7\datablogger_scraper\datablogger_scraper


Adding a class in the items.py file to create fields that will store the links that will be crawled.

In [ ]:
# %load items.py

# Define here the models for your scraped items
#
# See documentation in:
# http://doc.scrapy.org/en/latest/topics/items.html

import scrapy

class DatabloggerScraperItem(scrapy.Item):
    link_from = scrapy.Field()
    link_to = scrapy.Field()

    


In [5]:
cd spiders/

C:\Users\Sam\big-data-python-class\Homeworks\Homework7\datablogger_scraper\datablogger_scraper\spiders


Changing the code of the spider class that was generated automatically. The following class uses the Item class in the items.py file, extracts links and creates a list of objects of the class defined in the items.py file.

In [ ]:
# %load datablogger.py
# -*- coding: utf-8 -*-
import scrapy
from scrapy.linkextractor import LinkExtractor
from scrapy.spiders import Rule, CrawlSpider
from datablogger_scraper.items import DatabloggerScraperItem


class DatabloggerSpider(CrawlSpider):
    # The name of the spider
    name = "datablogger"
    allowed_domains = ["data-blogger.com"]
    start_urls = ["https://www.data-blogger.com/"]

    # This spider has one rule: extract all (unique and canonicalized) links, follow them and parse them using the parse_items method
    rules = [
        Rule(
            LinkExtractor(
                canonicalize=True,
                unique=True
            ),
            follow=True,
            callback="parse_items"
        )
    ]

    # Method which starts the requests by visiting all URLs specified in start_urls
    def start_requests(self):
        for url in self.start_urls:
            yield scrapy.Request(url, callback=self.parse, dont_filter=True)

    # Method for parsing items
    def parse_items(self, response):
        # The list of items that are found on the particular page
        items = []
        # Only extract canonicalized and unique links (with respect to the current page)
        links = LinkExtractor(canonicalize=True, unique=True).extract_links(response)
        # Now go through all the found links
        for link in links:
            # Check whether the domain of the URL of the link is allowed; so whether it is in one of the allowed domains
            is_allowed = False
            for allowed_domain in self.allowed_domains:
                if allowed_domain in link.url:
                    is_allowed = True
            # If it is allowed, create a new item and add it to the list of found items
            if is_allowed:
                item = DatabloggerScraperItem()
                item['link_from'] = response.url
                item['link_to'] = link.url
                items.append(item)
        # Return all the found items
        return items

Using the spider defined in the above file to crawl the url and then saving to a csv file.

In [36]:
%%cmd
scrapy crawl datablogger -o links.csv -t csv

Microsoft Windows [Version 10.0.17134.345]
(c) 2018 Microsoft Corporation. All rights reserved.

(base) C:\Users\Sam\big-data-python-class\Homeworks\Homework7\datablogger_scraper\datablogger_scraper\spiders>scrapy crawl datablogger -o links.csv -t csv

(base) C:\Users\Sam\big-data-python-class\Homeworks\Homework7\datablogger_scraper\datablogger_scraper\spiders>

C:\Users\Sam\big-data-python-class\Homeworks\Homework7\datablogger_scraper\datablogger_scraper\spiders\datablogger.py:8: ScrapyDeprecationWarning: Module `scrapy.linkextractor` is deprecated, use `scrapy.linkextractors` instead
  from scrapy.linkextractor import LinkExtractor
2018-11-11 11:17:58 [scrapy] INFO: Scrapy 1.2.0 started (bot: datablogger_scraper)
2018-11-11 11:17:58 [scrapy] INFO: Overridden settings: {'NEWSPIDER_MODULE': 'datablogger_scraper.spiders', 'FEED_URI': 'links.csv', 'SPIDER_MODULES': ['datablogger_scraper.spiders'], 'BOT_NAME': 'datablogger_scraper', 'ROBOTSTXT_OBEY': True, 'FEED_FORMAT': 'csv'}
2018-11-11 11:17:58 [scrapy] INFO: Enabled extensions:
['scrapy.extensions.feedexport.FeedExporter',
 'scrapy.extensions.logstats.LogStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.corestats.CoreStats']
2018-11-11 11:17:58 [scrapy] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.robotstxt.RobotsTxtMiddleware',
 'scrapy.downloader

7.2  Create a Stochastic matrix from its resulting crawling as per https://cs7083.wordpress.com/2013/01/31/demystifying-the-pagerank-and-hits-algorithms/

Creating Stochastic matrix using the results saved in the links.csv file. 

In [14]:
import pandas as pd
import numpy as np

lst = []
raw = pd.read_csv("links.csv")
r = raw['link_to'][0]
for i in range(len(raw)):
    if raw['link_to'][i] == r:
        lst.append(raw['link_from'][i])
    else:
        r = raw['link_to'][i]
        lst.append(r)
        
item = list(pd.DataFrame(lst)[0].unique())

link = []
length = len(lst)
for i, val in enumerate(lst):
    if i < length-1:
        link.append((lst[i], lst[i+1]))

n = pd.DataFrame(index=item, columns=item)
m = n.replace(np.NaN, 0)
for i in link:
    m.loc[i] = 1.0

ar = np.array(m)
v = ar.sum(axis=1)

result = ar/v[:, np.newaxis]
stochasticmatrix = np.nan_to_num(result)

stochasticmatrix

array([[0.        , 0.02702703, 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.16666667, 0.        , 0.16666667, ..., 0.        , 0.        ,
        0.        ],
       [0.16666667, 0.16666667, 0.        , ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.5       , 0.        ,
        0.        ]])

7.3 Pass it through the Page Rank algorithm and provide the list of the top 5 page URLs in your sample

In [25]:
import numpy as np

def pagerank(H):
    n = len(H)
    w = np.zeros(n)
    rho = 1./n * np.ones(n);
    for i in range(n):
        if np.multiply.reduce(H[i]== np.zeros(n)):
            w[i] = 1
    newH = H + np.outer((1./n * w),np.ones(n))
 
    theta=0.85
    G = (theta * newH) + ((1-theta) * np.outer(1./n * np.ones(n), np.ones(n)))
    #print rho
    for j in range(10):
        rho = np.dot(rho,G)
        #print rho
    
    return list(rho)

In [26]:
r = pagerank(stochasticmatrix)
value = ((pd.DataFrame(r)).sort_values(0, ascending=False)).head(5)
index = list(value.index)
index_int = map(int, index)
index_int

[9, 0, 34, 1, 12]

In [27]:
url = pd.DataFrame(item)
print "Top five URLs:"
for i in index_int:
    print url[0][i]

Top five URLs:
https://www.data-blogger.com/nl/
https://www.data-blogger.com/
https://www.data-blogger.com/2018/07/16/should-you-start-learning-python-in-2018-guide/
https://www.data-blogger.com/write-for-us/
https://www.data-blogger.com/author/admin/


7.x For extra credit use the hits algorithm ( with a connectivity matrix )

In [32]:
def hits(A):
    n= len(A)
    Au= np.dot(np.transpose(A),A)
    Hu = np.dot(A,np.transpose(A))
    a = np.ones(n)
    h = np.ones(n)
    for j in range(5):
        a = np.dot(a,Au)
        a= a/sum(a)
        h = np.dot(h,Hu)
        h = h/ sum(h)
    return h

In [33]:
value = pd.DataFrame(hits(ar))
sort = (value.sort_values(0, ascending=False)).head(5)
hit = list(sort.index)
url = pd.DataFrame(item)
print "Top 5 page URLs:"
for i in hit:
    print 'http://www.datablogger.com'+(url[0][i]).split('.com')[-1]

Top 5 page URLs:
http://www.datablogger.com/category/personal-projects/
http://www.datablogger.com/zh/
http://www.datablogger.com/category/security/
http://www.datablogger.com/author/admin/
http://www.datablogger.com/2018/02/15/creating-neural-networks-chainer/


7.xx For advanced credit find another ranking alogrithm and demonstrate that as well

In [ ]:
def salsa(L):
    Au= dot(transpose(L),L)
    Hu = dot(L,transpose(L))
    
    

### References

1. https://www.data-blogger.com/2016/08/18/scraping-a-website-with-python-scrapy/
2. https://cs7083.wordpress.com/2013/01/31/demystifying-the-pagerank-and-hits-algorithms/
3. https://mherman.org/blog/scraping-web-pages-with-scrapy/
4. https://mherman.org/blog/recursively-scraping-web-pages-with-scrapy/